In [0]:
%sql

select count(*) from bronze.txn_tbl

count(1) 10000

### Reading source data from bronze layer

In [0]:
Transaction_df = spark.read.table("bronze.txn_tbl")
customer_df = spark.read.table("bronze.customer_tbl")
branch_df = spark.read.table("bronze.branches_tbl")

#Cleansed and Enriched Data

#####1.Function to drop duplicates from each source dataframe

In [0]:
def remove_duplicates(input_df):

    deduplicated_df = input_df.dropDuplicates()
    return deduplicated_df

#####2.Function to remove all specified columns which can't be null

In [0]:
from functools import reduce
def remove_null_rows(input_df, columns_to_check):
    from pyspark.sql.functions import col
    
    # Filter rows where any specified column has null value
    condition = ~reduce(lambda x, y: x | y, (col(column).isNull() for column in columns_to_check))
    non_null_df = input_df.filter(condition)
    
    return non_null_df

#####3.Function to check valid customer

In [0]:
from pyspark.sql import functions as F

def check_customer_id_length(input_df, length):
    result_df = input_df.withColumn(
        "customer_id_length_valid",
        F.when(F.length(F.col("customer_id")) == length, "valid").otherwise("invalid"),
    )
    result_df = result_df.filter(col("customer_id_length_valid")=="valid")
    return result_df
  

#### Cleansing work 

###1.Removing Duplicates

In [0]:
txn_deduplicated_df = remove_duplicates(Transaction_df)
cust_deduplicated_df = remove_duplicates(customer_df)
branch_deduplicated_df = remove_duplicates(branch_df)

# Count the number of rows in each DataFrame
txn_count = txn_deduplicated_df.count()
cust_count = cust_deduplicated_df.count()
branch_count = branch_deduplicated_df.count()

# Print the counts
print(f"Transaction DataFrame Count: {txn_count}")
print(f"Customer DataFrame Count: {cust_count}")
print(f"Branch DataFrame Count: {branch_count}")


Transaction DataFrame Count: 5000
Customer DataFrame Count: 1000
Branch DataFrame Count: 10


##2. Dropping data if null value 

In [0]:
# List of columns to check for null values
columns_to_check = ["transaction_id", "customer_id"]

# Remove columns with only null values based on specified columns
txn_non_null_df = remove_null_rows(txn_deduplicated_df, columns_to_check)
txn_non_null_df.count()

Out[8]: 5000

##3.  Quality Check : on valid customer

In [0]:
from pyspark.sql.functions import col

# Specify the expected length of customer_id
expected_length = 5

# Apply the function to check customer_id length
verified_txn_df = check_customer_id_length(txn_non_null_df, expected_length)
verified_cust_df = check_customer_id_length(cust_deduplicated_df, expected_length)

# Count the number of rows in each DataFrame
txn_count = verified_txn_df.count()
cust_count = verified_cust_df.count()

# Print the counts
print(f"Transaction DataFrame Count: {txn_count}")
print(f"Customer DataFrame Count: {cust_count}")

Transaction DataFrame Count: 5000
Customer DataFrame Count: 1000


In [0]:
joined_df = Transaction_df.join(customer_df, on=['customer_id', 'customer_id'], how='inner').join(branch_df, on=['branch_id', 'branch_id'], how='inner')

In [0]:
joined_df.show()

+---------+---------+-----------+-----------+--------------+-------+----------------+------+--------+-------------------+---------+--------------------+--------------------+--------------+--------------------+------------+----------+-------------------+---------------+---------------+--------+
|branch_id|branch_id|customer_id|customer_id|transaction_id|channel|transaction_type|amount|currency|          timestamp|   status|                name|               email|         phone|             address|credit_score| join_date|        last_update|           name|       location|timezone|
+---------+---------+-----------+-----------+--------------+-------+----------------+------+--------+-------------------+---------+--------------------+--------------------+--------------+--------------------+------------+----------+-------------------+---------------+---------------+--------+
|    B0007|    B0007|      C1475|      C1475|         T8000| branch|         deposit|  3.88|     USD|2025-01-15 19:

In [0]:
joined_df = Transaction_df.alias('t') \
    .join(customer_df.alias('c'), col('t.customer_id') == col('c.customer_id'), 'left') \
    .join(branch_df.alias('b'), col('t.branch_id') == col('b.branch_id'), 'left') \
    .select(
        col('t.transaction_id'),
        col('t.channel'),
        col('t.transaction_type'),
        col('t.amount'),
        col('t.currency'),
        col('t.timestamp').alias('transaction_timestamp'),
        col('t.status').alias('transaction_status'),
        col('t.customer_id'),
        col('c.name').alias('customer_name'), # renamed column
        col('c.email'),
        col('c.phone'),
        col('c.address'),
        col('c.credit_score'),
        col('c.join_date'),
        col('c.last_update'),
        col('t.branch_id'),
        col('b.name').alias('branch_name'), # renamed column
        col('b.location').alias('branch_location'), # renamed column
        col('b.timezone').alias('branch_timezone') # renamed column
    )

In [0]:
joined_df.write.format("delta").mode("overwrite").saveAsTable("silver.merge_table")

In [0]:
joined_df.printSchema()

root
 |-- branch_id: string (nullable = true)
 |-- branch_id: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- customer_id: string (nullable = true)
 |-- transaction_id: string (nullable = true)
 |-- channel: string (nullable = true)
 |-- transaction_type: string (nullable = true)
 |-- amount: double (nullable = true)
 |-- currency: string (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- status: string (nullable = true)
 |-- name: string (nullable = true)
 |-- email: string (nullable = true)
 |-- phone: string (nullable = true)
 |-- address: string (nullable = true)
 |-- credit_score: long (nullable = true)
 |-- join_date: string (nullable = true)
 |-- last_update: string (nullable = true)
 |-- name: string (nullable = true)
 |-- location: string (nullable = true)
 |-- timezone: string (nullable = true)



In [0]:
flag_source_df = joined_df.select("transaction_id","amount","channel","timestamp","currency","address")

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import BooleanType
from pyspark.sql.functions import regexp_extract


# Regular expression pattern to extract 5-digit ZIP code at the end
zip_code_pattern = r'(\d{5})$'

# Add a new column 'zip_code' by applying the regular expression pattern
df_with_zip = flag_source_df.withColumn("zip_code", regexp_extract("address", zip_code_pattern, 1))

zip_codes_list = df_with_zip.select("zip_code").rdd.flatMap(lambda x: x).collect()


# Original list of zip codes
zip_codes_list = [f'{i:05d}' for i in range(1000)]  # Example list of zip codes

# Create a new list with the first 950 items 
new_zip_codes_list = zip_codes_list[:950]


# Function to check if the zip code exists in the predefined list
def check_zip_code(address):
    zip_code = address[-5:]  # Extract last 5 digits
    return zip_code in new_zip_codes_list

# Register the UDF with Spark
check_zip_code_udf = F.udf(check_zip_code, BooleanType())

In [0]:
from pyspark.sql import functions as F


flag_df = flag_source_df.select(
    F.col('transaction_id'),
    F.when(F.col('amount') > 90000, "unusual_amount")
     .when(F.col('currency').isin(['Cryptocurrency']), "watchlist_match")
     .when(check_zip_code_udf(F.col('address')), "new_geolocation")
     .when(F.col('amount') < 2, "pattern_anomaly")
     .otherwise("normal")  
     .alias('flag_type'),
    F.current_timestamp().alias('timestamp')
)

flag_type_df = flag_df.withColumn(
    'confidence_score',
    F.when(F.col('flag_type') == 'unusual_amount', 0.75)
     .when(F.col('flag_type') == 'Watchlist_match', 0.95)
     .when(F.col('flag_type') == 'new_geolocation', 0.80)
     .when(F.col('flag_type') == 'pattern_anomaly', 0.70)          
     .otherwise(0.5)  # Default confidence score for other cases
)

flagged_df = flag_type_df.filter(F.col("flag_type") != "normal")


flag_id_df = flagged_df.withColumn(
    'flag_id',
    F.concat(F.lit("F000"), F.monotonically_increasing_id())
)


# Reorder the columns
ordered_columns = ['flag_id', 'transaction_id', 'flag_type', 'timestamp', 'confidence_score']
df_ordered = flag_id_df.select(ordered_columns)

# Write the DataFrame to a Delta table
df_ordered.write.format("delta").mode("overwrite").saveAsTable("silver.fraud_flag")


In [0]:
%sql
select distinct flag_type,count(*) from silver.fraud_flag group by flag_type limit 10;

flag_type count(1) new_geolocation 28 pattern_anomaly 110 unusual_amount 60

In [0]:
%sql
select * from silver.fraud_flag limit 10;

flag_id transaction_id flag_type timestamp confidence_score F0000 T8003 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7 F0001 T8031 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7 F0002 T8038 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7 F0003 T8050 new_geolocation 2024-08-02T09:35:08.513+0000 0.8 F0004 T8103 unusual_amount 2024-08-02T09:35:08.513+0000 0.75 F0005 T8183 unusual_amount 2024-08-02T09:35:08.513+0000 0.75 F0006 T8243 unusual_amount 2024-08-02T09:35:08.513+0000 0.75 F0007 T8260 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7 F0008 T8300 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7 F0009 T8312 pattern_anomaly 2024-08-02T09:35:08.513+0000 0.7

####Customer segment table

In [0]:
def filter_recent_customers(join_date_col):
    # Calculate the date one month ago
    one_month_ago = F.date_sub(F.current_date(), 30)
    
    # Return a boolean condition for recent customers
    return F.col(join_date_col) >= one_month_ago

  

In [0]:
def filter_old_customers(join_date_col):
    # Calculate the date 90 days ago
    ninety_days_ago = F.date_sub(F.current_date(), 90)
    
    # Return a boolean condition for customers older than 90 days
    return F.col(join_date_col) <= ninety_days_ago

In [0]:
from pyspark.sql.functions import *
 
# joined_df = joined_df.withColumn("year_diff", months_between(col("timestamp"), col("join_date")) / 12)


joined_yr_df = joined_df.withColumn("years_diff", round(datediff(col("timestamp").cast("timestamp"), to_date(col("join_date"), "yyyy-MM-dd")) / lit(365.25)))




In [0]:
joined_yr_df.display(10)

branch_id branch_id customer_id customer_id transaction_id channel transaction_type amount currency timestamp status name email phone address credit_score join_date last_update name location timezone years_diff B0007 B0007 C1475 C1475 T8000 branch deposit 3.88 USD 2025-01-15T19:41:00.000+0000 completed Chase Ellis chase.ellis@aol.com (573) 602-0647 180 Bradley Harbor Suite 169, East Julie, VA 98352 809 2021-08-29 2024-07-26 00:00:00 North Branch Richardsmouth PST 3.0 B0005 B0005 C1564 C1564 T8001 web payment 21.34 USD 2025-01-16T03:02:00.000+0000 completed Melanie Solis melanie.solis@outlook.com (149) 795-0558 23455 Tara Club Apt. 739, South Lucasville, NC 75728 554 2022-02-09 2024-07-30 00:00:00 West Branch New Shawnashire AEST 3.0 B0004 B0004 C1721 C1721 T8002 web transfer 43.89 GBP 2025-01-16T04:39:00.000+0000 completed Bradley Robbins bradley.robbins@gmail.com (178) 730-0285 363 Brown Fords Suite 069, South Jamesfort, AS 98431 542 2022-12-28 2024-07-28 00:00:00 West Branch North Elizabeth EST 2.0 B0006 B0006 C1826 C1826 T8003 mobile withdrawal 1.0 USD 2025-01-16T16:16:00.000+0000 completed Blake Dixon blake.dixon@aol.com (126) 466-0935 860 Peter Lane Apt. 355, Bellport, AK 33748 675 2023-08-13 2024-07-23 00:00:00 North Branch Lake Lindsey GMT 1.0 B0006 B0006 C1604 C1604 T8004 branch transfer 314.98 USD 2025-01-16T21:34:00.000+0000 completed Henry Brown henry.brown@gmail.com (169) 469-4356 50187 Tonya Circles Suite 246, New Stevenborough, OK 18247 768 2022-04-28 2024-07-28 00:00:00 North Branch Lake Lindsey GMT 3.0 B0008 B0008 C1221 C1221 T8005 web payment 136.33 GBP 2025-01-17T00:41:00.000+0000 completed Mr. Andrew Novak DDS mr..dds@gmail.com (235) 982-3440 49916 Smith Circle Apt. 064, Lake Douglasville, NJ 37721 780 2020-04-08 2024-07-29 00:00:00 West Branch New Robert AEST 5.0 B0001 B0001 C1237 C1237 T8006 ATM deposit 23.27 EUR 2025-01-17T06:43:00.000+0000 completed Christopher Smith christopher.smith@outlook.com (901) 628-2484 07006 Beck Creek Apt. 422, Robertland, PW 10007 668 2020-05-08 2024-07-28 00:00:00 North Branch Port Luistown AEST 5.0 B0000 B0000 C1705 C1705 T8007 ATM transfer 21.7 GBP 2025-01-17T10:42:00.000+0000 completed Crystal Wilson crystal.wilson@aol.com (757) 973-6298 2720 Justin Mission Apt. 025, Michaelmouth, DE 70671 706 2022-11-11 2024-07-25 00:00:00 Downtown Branch Jacksonborough AEST 2.0 B0008 B0008 C1055 C1055 T8008 web withdrawal 9.12 EUR 2025-01-17T14:20:00.000+0000 completed Elizabeth Franklin elizabeth.franklin@gmail.com (153) 052-2793 899 Alvarez Radial Apt. 171, Hillfort, IN 39249 837 2019-04-29 2024-07-21 00:00:00 West Branch New Robert AEST 6.0 B0001 B0001 C1962 C1962 T8009 branch withdrawal 123.93 GBP 2025-01-17T22:08:00.000+0000 completed Cathy Larson cathy.larson@yahoo.com (997) 568-9516 USNV Gonzalez, FPO AP 47526 553 2024-05-19 2024-07-20 00:00:00 North Branch Port Luistown AEST 1.0 B0000 B0000 C1651 C1651 T8010 branch payment 15.96 EUR 2025-01-18T00:58:00.000+0000 completed Chad Mckenzie chad.mckenzie@outlook.com (001) 770-3669 801 Crane Estate, Franklintown, IL 73977 809 2022-07-14 2024-07-20 00:00:00 Downtown Branch Jacksonborough AEST 3.0 B0002 B0002 C1881 C1881 T8011 mobile transfer 31.44 GBP 2025-01-18T05:48:00.000+0000 completed Marcus Nelson marcus.nelson@aol.com (479) 771-4615 Unit 9326 Box 9578, DPO AE 24573 804 2023-12-19 2024-07-30 00:00:00 North Branch New Meganfort GMT 1.0 B0007 B0007 C1683 C1683 T8012 web deposit 16.37 EUR 2025-01-18T14:51:00.000+0000 pending Jason Williams jason.williams@outlook.com (161) 929-2247 90605 Nancy Harbors, South Roberto, FL 39293 770 2022-10-07 2024-07-30 00:00:00 North Branch Richardsmouth PST 2.0 B0001 B0001 C1947 C1947 T8013 mobile transfer 25.0 GBP 2025-01-18T19:54:00.000+0000 completed Kayla Mendez kayla.mendez@gmail.com (793) 318-7033 585 Michael Pines Apt. 796, New Marietown, IN 13505 673 2024-04-22 2024-07-27 00:00:00 North Branch Port Luistown AEST 1.0 B0005 B0005 C1676 C1676 T8014 web deposit 67.52 EUR 2025-01-18T22:57:00.000+000

In [0]:

from pyspark.sql.functions import col,when

cust_seg_df = joined_yr_df.select(
    F.col('customer_id'),
    F.col('join_date'),
    F.when(filter_recent_customers('join_date'), "New_User")
     .when(filter_old_customers('last_update'), "Inactive")
     .when(F.col('amount') > 90000, "High_Value")
     .when(F.col('years_diff') > 5, "Loyal")
     .when(F.col('credit_score') < 550, "Credit_Risk")
     .otherwise("normal")  
     .alias('segment_name'),
    F.current_timestamp().alias('last_updated_date')
)

cust_seg_id_df = cust_seg_df.filter(F.col("segment_name") != "normal")


cust_seg_final_df = (
    cust_seg_id_df
    .withColumn(
        'segment_description',
        when(col("segment_name") == "High_Value", "Customers with high transaction volume")
        .when(col("segment_name") == "New_User", "Customers who joined in last 30 days")
        .when(col("segment_name") == "Inactive", "No transactions in last 90 days")
        .when(col("segment_name") == "Credit_Risk", "Customers with low credit scores")
        .when(col("segment_name") == "Loyal", "Consistent activity for over 5 years")
        .otherwise("Unknown")
    )
)

# Reorder the columns
ordered_columns = [ 'customer_id', 'segment_name', 'segment_description', 'last_updated_date']
df_ordered = cust_seg_final_df.select(ordered_columns)

# Write the DataFrame to a Delta table
df_ordered.write.format("delta").mode("overwrite").saveAsTable("silver.customer_segments")


In [0]:
%sql
select distinct segment_name,count(*) from silver.customer_segments group by segment_name ;

segment_name count(1) High_Value 58 Loyal 882 Credit_Risk 1308 New_User 88